In [82]:
import requests, json
from collections import OrderedDict
from operator import getitem
import time
import datetime
import pandas as pd
import warnings
import math
from web3 import Web3
from ens import ENS
import plotly.express as px
pd.options.plotting.backend = 'plotly'

In [83]:
AMBERDATA_API_KEY = 'API KEY HERE'

In [84]:
headers = {
    "accept": "application/json",
    "x-amberdata-blockchain-id": "ethereum-mainnet",
    "x-api-key": f'{AMBERDATA_API_KEY}' ##ENTER YOUR API KEY
}

In [85]:
amberdata_rpc_url = f'https://rpc.web3api.io/api/v2?x-api-key={AMBERDATA_API_KEY}'

## Analyzing stETH APR

In [86]:
#Empyt dict for storing returned data and an ID. 
collection = {}
id = 0
#For Pagination
pagination = 0
total_pages_required = 30
contract_address = '0x442af784a788a5bd6f42a01ebe9f287a871243fb'  ##Lido Oracle Contract
topic = '0xdafd48d1eba2a416b2aca45e9ead3ad18b84e868fa6d2e1a3048bfd37ed10a32' ## Event signature: BeaconReported

In [87]:
##Fetch event data to calculat the APY of Lido and ETH2.0 Staking
while pagination <= total_pages_required:
    #Fetch Contract Events Logs. 
    url = f'https://web3api.io/api/v2/addresses/{contract_address}/logs?topic={topic}&page={pagination}&size=50'
    response = requests.request("GET", url, headers=headers)
    while response.status_code == 429:
        time.sleep(1)
        response = requests.request("GET", url, params=querystring)
    batch_list = json.loads(response.text)["payload"]['records']
    for item in batch_list:
        try: 
            id = id+1
            collection[id] = {}
            collection[id]["timestamp"] = item['timestamp']
            collection[id]['postTotalPooledEther'] =float.fromhex(item['data'][0])
            collection[id]['preTotalPooledEther'] =float.fromhex(item['data'][1])
            collection[id]['timeElasped'] =float.fromhex(item['data'][2])
        except NameError:
            print(NameError)
    print('Finished page',pagination, total_pages_required, id)
    pagination += 1

Finished page 0 30 50
Finished page 1 30 100
Finished page 2 30 150
Finished page 3 30 200
Finished page 4 30 250
Finished page 5 30 300
Finished page 6 30 350
Finished page 7 30 400
Finished page 8 30 450
Finished page 9 30 500
Finished page 10 30 550
Finished page 11 30 600
Finished page 12 30 650
Finished page 13 30 657
Finished page 14 30 657
Finished page 15 30 657
Finished page 16 30 657
Finished page 17 30 657
Finished page 18 30 657
Finished page 19 30 657
Finished page 20 30 657
Finished page 21 30 657
Finished page 22 30 657
Finished page 23 30 657
Finished page 24 30 657
Finished page 25 30 657
Finished page 26 30 657
Finished page 27 30 657
Finished page 28 30 657
Finished page 29 30 657
Finished page 30 30 657


In [88]:
#Formatting data and calculating APR
df = pd.DataFrame.from_dict(collection,orient='index')
df['date'] = pd.to_datetime(df['timestamp'], unit='ms')
df['protocol_apr'] = (df["postTotalPooledEther"] - df["preTotalPooledEther"]) *365*24*60*60 / (df["preTotalPooledEther"]*df["timeElasped"])*100
df['lido_staking_apr'] = (df["postTotalPooledEther"] - df["preTotalPooledEther"]) *365*24*60*60 / (df["preTotalPooledEther"]*df["timeElasped"])*.9*100
df = df.set_index('date')

In [89]:
#Plotting the difference between Lido APR & Beacon chain APR. 
df[['protocol_apr', "lido_staking_apr"]].plot()

## stETH Holder Analysis

In [90]:
# Connecting to Amberdata RPC for ENS Domains
w3 = Web3(Web3.HTTPProvider(amberdata_rpc_url))
print(w3.is_connected()) #Check you are connected. 

True


In [91]:
#create ENS object
ns = ENS.from_web3(w3)

In [93]:
#Empyt dict for storing returned data and an ID. 
collection2 = {}
id = 0
#For Pagination
pagination = 0
total_pages_required = 50
stETH_address = '0xae7ab96520DE3A18E5e111B5EaAb095312D7fE84'  ##stETH token address


In [94]:
while pagination <= total_pages_required:
    #Fetch Contract Events Logs. 
    url = f'https://web3api.io/api/v2/tokens/{stETH_address}/holders/latest?page={pagination}&size=1000'
    response = requests.request("GET", url, headers=headers)
    while response.status_code == 429:
        time.sleep(1)
        response = requests.request("GET", url, params=querystring)
    batch_list = json.loads(response.text)["payload"]['records']
    for item in batch_list:
        try: 
            id = id+1
            collection2[id] = {}
            collection2[id]["tokenAddress"] = item['tokenAddress']
            collection2[id]['holderAddress'] = item['holderAddress']
            #collection2[id]['ens'] = ns.name(item['holderAddress']) - ENS lookup will slow the process. Uncomment if you'd like to get ENS addresses
            collection2[id]['timestamp'] = item['timestamp']
            collection2[id]['numTokens'] = float(item['numTokens']) / math.pow(10,18)
        except NameError:
            print(NameError)
    print('Finished page',pagination, total_pages_required, id)
    pagination += 1

Finished page 0 50 1000
Finished page 1 50 2000
Finished page 2 50 3000
Finished page 3 50 4000
Finished page 4 50 5000
Finished page 5 50 6000
Finished page 6 50 7000
Finished page 7 50 8000
Finished page 8 50 9000
Finished page 9 50 10000
Finished page 10 50 11000
Finished page 11 50 12000
Finished page 12 50 13000
Finished page 13 50 14000
Finished page 14 50 15000
Finished page 15 50 16000
Finished page 16 50 17000
Finished page 17 50 18000
Finished page 18 50 19000
Finished page 19 50 20000
Finished page 20 50 21000
Finished page 21 50 22000
Finished page 22 50 23000
Finished page 23 50 24000
Finished page 24 50 25000
Finished page 25 50 26000
Finished page 26 50 27000
Finished page 27 50 28000
Finished page 28 50 29000
Finished page 29 50 30000
Finished page 30 50 31000
Finished page 31 50 32000
Finished page 32 50 33000
Finished page 33 50 34000
Finished page 34 50 35000
Finished page 35 50 36000
Finished page 36 50 37000
Finished page 37 50 38000
Finished page 38 50 39000
Finis

In [95]:
#Formatting data to dataframe
df2 = pd.DataFrame.from_dict(collection2,orient='index')
df2['date'] = pd.to_datetime(df2['timestamp'], unit='ms')
df2['numTokens'] = df2['numTokens'].round(3)

In [97]:
fig = px.pie(df2, values='numTokens', names='holderAddress', title='Population of European continent')
fig.show()